In [1]:
import h5py
from os.path import join
import numpy as np

from mssa_learning.mssa import MSSA
from mssa_learning.tools.plot import *
from mssa_learning.tools.preprocessing import *
from mssa_learning.tools.postprocessing import *

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
import plotly.plotly as py

import progressbar
import scipy.io

/usr/local/lib/python2.7/dist-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


In [2]:
def extract_data(p, a, r, c):
    multiple_data = []
    for i in p:
        for j in a:
            for k in r:
                for l in c:
                    key = "P" + str(i).zfill(3) + "R" + str(k).zfill(3) + "A" + str(j).zfill(3)
                    if str(l) not in h5_data[key].keys():
                        print("Camera data not included change person, action, repetition or camera")
                    else:
                        multiple_data.append(h5_data[key][str(l)])
    return multiple_data

In [3]:
def extract_kalman_data(p, a, r):
    multiple_data = []
    for i in p:
        for j in a:
            for k in r:
                key = "P" + str(i).zfill(3) + "R" + str(k).zfill(3) + "A" + str(j).zfill(3)
                multiple_data.append(h5_kalman[key]["thetas"])
    return multiple_data

In [4]:
init_notebook_mode(connected=True)

In [5]:
h5_data = h5py.File(join("..", "data", "dataset_converted" , "h5", "poses.h5"))

In [6]:
mssa = MSSA()

### MSSA on single time serie

In [26]:
p = [1]  # person
a = [3]  # action
r = [1]  # repetition
c = [1]  # camera

In [27]:
multiple_data = extract_data(p, a, r, c)

In [28]:
multiple_data = rebase(multiple_data)

In [29]:
data = transpose(multiple_data)[0]

In [30]:
fig = plot_timeseries(data)
iplot(fig)

py.image.save_as(fig, filename='../figures/example.png')

In [45]:
max_var = 0
index = 0
joints = get_joint_names(True)
blocked = ["HandRight", "HandLeft", "HandTipRight", "HandTipLeft", "ThumbRight", "ThumbLeft"]

for i, d in enumerate(data):
    var = abs(d[-1] - d[0])
    joint = joints[int(i / 3)]
    if joint not in blocked:
        if var > max_var:
            max_var = var
            index = i
print index, max_var

28 0.37084638920919044


In [46]:
joint = get_joint_names(True)[int(index / 3)]
print joint

WristRight


#### Compute principal components

In [12]:
pc, eig_vec, eig_val = mssa.compute_principal_components(data)

In [13]:
fig = plot_principal_components([pc])
iplot(fig)
py.image.save_as(fig, filename='../figures/pc.png')

In [14]:
fig = plot_explained_variance(eig_val, 10)
iplot(fig)

#### Reconstruct signal

In [15]:
rs_data = mssa.reconstruct_signal(pc, eig_vec, 10)

In [16]:
fig = plot_timeseries(data, rs_data)
iplot(fig)
py.image.save_as(fig, filename='../figures/reconstruction.png')

#### Calculate distance

In [17]:
dist = []
lengths = []
for n in range(1, 25):
    rs_data = mssa.reconstruct_signal(pc, eig_vec, n)
    dist.append(mssa.signal_distance(data, np.array(rs_data)))
    rs_data = transpose([rs_data])[0]
    lengths.append(calculate_lengths(rs_data))

In [18]:
trace = go.Scatter(
    x = np.arange(len(dist)) + 1,
    y = dist
)
iplot([trace])

In [19]:
joint_name = "rmain"

length_data = []
for i in range(len(lengths)):
    trace = go.Scatter(
        x = np.arange(len(lengths[i][joint_name])),
        y = lengths[i][joint_name]
    )
    length_data.append(trace)
    
length = calculate_lengths(multiple_data[0])
trace = go.Scatter(
            x = np.arange(len(length[joint_name])),
            y = length[joint_name]
        )
length_data.append(trace)
iplot(length_data)

### MSSA on several repetition

In [20]:
p = [1]  # people
a = [1]  # action
r = [1, 2]  # repetition
c = [1]  # camera

In [21]:
multiple_data = extract_data(p, a, r, c)

In [22]:
multiple_data = rebase(multiple_data)

In [23]:
multiple_data = transpose(multiple_data)

In [24]:
pcs = []
for data in multiple_data:
    pc, eig_vec,_ = mssa.compute_principal_components(data)
    pcs.append(pc[:,:10])

In [25]:
fig = plot_principal_components(pcs)
iplot(fig)

### MSSA on several people

In [28]:
p = [1, 9, 4, 15]  # people
a = [1]  # action
r = [1]  # repetition
c = [1]  # camera

In [29]:
multiple_data = extract_data(p, a, r, c)

In [30]:
multiple_data = rebase(multiple_data)

In [31]:
multiple_data = transpose(multiple_data)

In [32]:
pcs = []
for data in multiple_data:
    pc, eig_vec,_ = mssa.compute_principal_components(data)
    pcs.append(pc[:,:10])

In [33]:
fig = plot_principal_components(pcs)
iplot(fig)

### MSSA on several actions

In [34]:
p = [1]  # people
a = [1, 5, 9, 3]  # action
r = [1]  # repetition
c = [1]  # camera

In [35]:
multiple_data = extract_data(p, a, r, c)

In [36]:
multiple_data = rebase(multiple_data)

In [37]:
multiple_data = transpose(multiple_data)

In [38]:
pcs = []
for data in multiple_data:
    pc, eig_vec,_ = mssa.compute_principal_components(data)
    pcs.append(pc[:, :10])

In [39]:
fig = plot_principal_components(pcs)
iplot(fig)

### MSSA on Kalman theta

In [40]:
h5_kalman = h5py.File(join("..", "data", "dataset_converted" , "h5", "kalman.h5"))

In [41]:
p = [1]  # people
a = [1]  # action
r = [1]  # repetition
c = [1]  # camera

In [42]:
multiple_data = extract_kalman_data(p, a, r)

In [43]:
data = transpose(multiple_data)[0]

In [44]:
pc, eig_vec, eig_val = mssa.compute_principal_components(data)

In [45]:
fig = plot_principal_components([pc])
iplot(fig)

In [46]:
fig = plot_explained_variance(eig_val, 10)
iplot(fig)

In [47]:
rs_data = mssa.reconstruct_signal(pc, eig_vec, 10)

In [48]:
fig = plot_timeseries(data, rs_data)
iplot(fig)

### Timeserie + Noise

In [49]:
p = [1]  # people
a = [1]  # action
r = [1]  # repetition
c = [1]  # camera

In [50]:
multiple_data = extract_data(p, a, r, c)

In [51]:
multiple_data = rebase(multiple_data)

In [52]:
multiple_data = transpose(multiple_data)

In [53]:
noise_data = []
N = len(multiple_data[0][0])
D = int(len(multiple_data[0])) 
mean = np.zeros(D)
cov = np.identity(D)*0.0001

for i in range(2):
    noise = np.random.multivariate_normal(mean, cov, N).T
    noise_data.append(multiple_data[0] + noise)

In [54]:
fig = plot_timeseries(multiple_data[0], noise_data[0])
iplot(fig)

In [55]:
pcs = []
eig_basis = []
eig_values = []
for data in noise_data:
    pc, eig_vec, eig_val = mssa.compute_principal_components(data)
    pcs.append(pc[:, :10])
    eig_basis.append(eig_vec)
    eig_values.append(eig_val)

In [57]:
I = eig_basis[0].T * eig_basis[1]

In [58]:
I

array([[-6.38774320e-11, -1.61901408e-08,  1.43660604e-07, ...,
        -0.00000000e+00, -0.00000000e+00, -0.00000000e+00],
       [ 5.60398309e-09, -6.51338869e-07,  3.69272749e-06, ...,
         4.01222649e-04, -1.30712257e-03,  4.21632214e-04],
       [-1.97131581e-09,  3.07321711e-07, -4.80266426e-06, ...,
        -3.22507909e-03, -8.51875068e-03,  1.20020993e-04],
       ...,
       [-0.00000000e+00,  1.32477284e-04, -7.45005620e-03, ...,
         1.91626198e-05,  1.54016819e-05,  1.08055819e-04],
       [-0.00000000e+00, -8.05506303e-04, -1.10525349e-02, ...,
        -5.18080202e-05,  2.66946962e-05,  5.84843554e-05],
       [-0.00000000e+00,  9.44904846e-04,  8.48748194e-03, ...,
        -7.23650754e-05,  6.98315924e-06,  4.45689998e-06]])